**!!!!!!!!!!!!! RUN AND RESTART SESSION !!!!!!!!!!!!!!!**

In [2]:
## !!!!!!!!!!!!! RUN AND RESTART SESSION !!!!!!!!!!!!!!!

%%capture
!pip install bitsandbytes accelerate transformers-interpret shap inseq
!pip install -U captum
!pip install transformers
!pip install --upgrade scipy==1.12
!pip install -U datasets

## !!!!!!!!!!!!! RUN AND RESTART SESSION !!!!!!!!!!!!!!!

In [1]:
import inseq
from datasets import load_dataset
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

### Load Dataset and sample

In [2]:
dataset = load_dataset("EdinburghNLP/xsum")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/6.24k [00:00<?, ?B/s]

xsum.py:   0%|          | 0.00/5.76k [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/304M [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/16.7M [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/17.0M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/204045 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/11332 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/11334 [00:00<?, ? examples/s]

In [3]:
# Few-shot examples from training set
train_examples = dataset["train"].select(range(2))

# Sample a subset of the test set for evaluation
test_sample = dataset["test"].select(range(1))
references = [example["summary"] for example in test_sample]

### Load MODEL and Tokenizer

In [4]:
model_name = "google/flan-t5-base"
tokenizer = AutoTokenizer.from_pretrained(model_name, model_max_length=2000)
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)

tokenizer_config.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.20k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.40k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/990M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

### Zero-Shot, One-Shot and Few-Shot

In [5]:
def build_zero_shot_prompt(doc):
    """Builds a zero-shot prompt."""
    prompt_template = "Please write a short summary of the following article:\n\n{}"
    return prompt_template.format(doc)

def build_one_shot_prompt(doc, train_example):
    """Builds a one-shot prompt with one example."""
    prompt = ""
    prompt += "Task: Summarize the input text. An example is provided below. \n"
    prompt += f"### EXAMPLE:\nDocument: {train_example['document'].strip()}\nSummary: {train_example['summary'].strip()}\n\n"
    prompt += f"### INPUT TEXT:\nDocument: {doc.strip()}\nSummary:[Fill the summary]"
    return prompt

def build_few_shot_prompt(doc, few_shots):
    """Builds a few-shot prompt with multiple examples."""
    prompt = ""
    prompt += "Task: Summarize the input text. Examples are provided below. \n"
    for ex in few_shots:
        prompt += f"### EXAMPLE:\nDocument: {ex['document'].strip()}\nSummary: {ex['summary'].strip()}\n\n"
    prompt += f"### INPUT TEXT:\nDocument: {doc.strip()}\nSummary:[Fill the summary]"
    return prompt

In [6]:
document = test_sample[0]["document"]

zero_shot_prompt = build_zero_shot_prompt(document)
one_shot_prompt = build_one_shot_prompt(document, train_examples[0])
few_shot_prompt = build_few_shot_prompt(document, train_examples)

### Explanation of different promptings

In [7]:
qa_model = inseq.load_model("google/flan-t5-base", "input_x_gradient", tokenizer=tokenizer)

# Apply model with the different prompts
out_zero_shot = qa_model.attribute(zero_shot_prompt, attribute_target=True, step_scores=["probability"], generation_args={"max_new_tokens": 128})
out_one_shot = qa_model.attribute(one_shot_prompt, attribute_target=True, step_scores=["probability"], generation_args={"max_new_tokens": 128})
out_few_shot = qa_model.attribute(few_shot_prompt, attribute_target=True, step_scores=["probability"], generation_args={"max_new_tokens": 128})

The following generation flags are not valid and may be ignored: ['output_attentions']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['output_attentions']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Attributing with input_x_gradient...: 100%|██████████| 32/32 [13:20<00:00, 25.83s/it]


In [8]:
print("--- Zero-Shot Output ---")
# Access the generated text (using .target.text as corrected previously)
generated_zero_shot = out_zero_shot.info["generated_texts"][0]
print(generated_zero_shot)
print("-" * 20) # Separator

print("--- One-Shot Output ---")
# Access the generated text
generated_one_shot = out_one_shot.info["generated_texts"][0]
print(generated_one_shot)
print("-" * 20) # Separator

print("--- Few-Shot Output ---")
# Access the generated text
generated_few_shot = out_few_shot.info["generated_texts"][0]
print(generated_few_shot)
print("-" * 20) # Separator

--- Zero-Shot Output ---
A charity has said it is "disappointing" that some prison leavers are not getting the support they need to find accommodation.
--------------------
--- One-Shot Output ---
A charity has said it is "disappointing" that some prisoners are not getting the support they need to find accommodation.
--------------------
--- Few-Shot Output ---
A charity has said it is "disappointing" that some prison leavers are not getting the support they need to find accommodation.
--------------------


In [57]:
out_zero_shot.aggregate("subwords", aggregate_target=False).show()

In [58]:
out_one_shot.aggregate("subwords", aggregate_target=False).show()

In [59]:
out_few_shot.aggregate("subwords", aggregate_target=False).show()